In [9]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import  make_subplots


In [10]:
dfA = pd.read_excel('Prop_testdata.xlsx',sheet_name=0)
dfB = pd.read_excel('Prop_testdata.xlsx',sheet_name=1)

**QUICK LOOK AT THE DATA**


In [11]:

thrustA = go.Scatter(x=dfA['Motor Optical Speed (RPM)'],y=dfA['Thrust (kgf)'],
                          mode='markers',
                          name='Thrust')
torqueA = go.Scatter(x=dfA['Motor Optical Speed (RPM)'],y=dfA['Torque (N·m)'],
                          mode='markers',
                          name='Torque')
efficiencyA = go.Scatter(x=dfA['Motor Optical Speed (RPM)'],y=dfA['Overall Efficiency (kgf/W)'],
                          mode='markers',
                          name='Efficiency')
figA = make_subplots(rows=1,cols=3)
figA.add_trace(thrustA,row=1,col=1)
figA.add_trace(torqueA,row=1,col=2)
figA.add_trace(efficiencyA,row=1,col=3)


thrustB = go.Scatter(x=dfB['Motor Optical Speed (RPM)'],y=dfB['Thrust (kgf)'],
                          mode='markers',
                          name='Thrust')
torqueB = go.Scatter(x=dfB['Motor Optical Speed (RPM)'],y=dfB['Torque (N·m)'],
                          mode='markers',
                          name='Torque')
efficiencyB = go.Scatter(x=dfB['Motor Optical Speed (RPM)'],y=dfB['Overall Efficiency (kgf/W)'],
                          mode='markers',
                          name='Efficiency')
figB = make_subplots(rows=1,cols=3)
figB.add_trace(thrustB,row=1,col=1)
figB.add_trace(torqueB,row=1,col=2)
figB.add_trace(efficiencyB,row=1,col=3)

figA.update_layout(title='Propeller A',
                   xaxis_title='RPM',
                   legend_title="Measured")
figB.update_layout(title='Propeller B',
                   xaxis_title='RPM',
                   legend_title="Measured")
figA.show()
figB.show()


**CREATE POLYNOMIAL MODEL**

In [12]:
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import LinearRegression
from sklearn.pipeline import make_pipeline
import numpy as np
properties = ['Thrust (kgf)', 'Torque (N·m)', 'Overall Efficiency (kgf/W)']

goA = dict(zip(properties ,[thrustA,torqueA,efficiencyA]))
goB = dict(zip(properties ,[thrustB,torqueB,efficiencyB]))
goTotal = [goA,goB]

degree = 2
polyreg = make_pipeline(PolynomialFeatures(degree),LinearRegression())

In [13]:
df = [dfA,dfB]
predict_5000 = np.zeros((2,3))
for ind,d in enumerate(df):
    X = d['Motor Optical Speed (RPM)'].values.reshape(-1,1)
    X_range = pd.DataFrame(np.linspace(X.min(), X.max(),10000)).values.reshape(-1,1)

    fig = make_subplots(rows=len(properties), cols=1)
    for i,p in enumerate(properties,start=1):
        y = d[p]
        polyreg.fit(X,y)
        fig.add_trace(goTotal[ind][p],row=i,col=1)
        y_pred = polyreg.predict(X_range)
        fig.add_trace(go.Scatter(x=X_range.flatten(),y=y_pred,mode='lines',name='predict ' + p),row=i,col=1)
        predict_5000[ind][i-1] = polyreg.predict([[5000]])
        fig.update_xaxes(title_text='RPM', row=i,col=1)
        fig.update_yaxes(title_text=p, row=i,col=1)
    fig.update_layout(title_text='Propeller ' + str(ind + 1) ,height=800, width=1000)
    fig.show()
print('Propeller A at 5000 RPM has efficiency: ', predict_5000[0][2], 'kgf/W')
print('Propeller B at 5000 RPM has efficiency: ', predict_5000[1][2], 'kgf/W' )

Propeller A at 5000 RPM has efficiency:  0.009003652011629927 kgf/W
Propeller B at 5000 RPM has efficiency:  0.009550684650317425 kgf/W


We can conclude from the prediction of our model that, propeller B has higher efficiency compared with propeller A at
the same 5000 RPM condition.

In [14]:
print('Predicted thrust of propeller B at 5000 RPM:', predict_5000[1][0], 'kgf')
print('Predicted torque of propeller B at 5000 RPM:', predict_5000[1][1], 'N.m')


Predicted thrust of propeller B at 5000 RPM: 0.24338501597562126 kgf
Predicted torque of propeller B at 5000 RPM: 0.03787945578550135 N.m
